In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')

import folium
import h3
import pandas as pd
import numpy as np
import branca.colormap as cm

# Set style
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")

# Configure pandas display options
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)


In [45]:
# Load all datasets
years = range(2016, 2024)
datasets = {}

for year in years:
    try:
        df = pd.read_csv(f'final{year}.csv')
        datasets[year] = df
        print(f"Loaded {year}: {len(df):,} records")
    except FileNotFoundError:
        print(f"File for {year} not found")

print(f"\nTotal datasets loaded: {len(datasets)}")


Loaded 2016: 157,422 records
Loaded 2017: 32,576 records
Loaded 2018: 31,311 records
Loaded 2019: 32,041 records
Loaded 2020: 20,464 records
Loaded 2021: 35,424 records
Loaded 2022: 33,147 records
Loaded 2023: 15,564 records

Total datasets loaded: 8


In [38]:
all_data.to_csv("ALL_DATA.csv",index=False)

In [46]:
# Combine all datasets
all_data = pd.concat(datasets.values(), ignore_index=True)
print(f"Combined dataset shape: {all_data.shape}")
print(f"Date range: {all_data['anio'].min()} - {all_data['anio'].max()}")

# Display basic info
print("\nDataset Info:")
print(all_data.info())

print("\nFirst few rows:")
all_data.head()


Combined dataset shape: (357949, 8)
Date range: 2016.0 - 2023.0

Dataset Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 357949 entries, 0 to 357948
Data columns (total 8 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   anio                 357949 non-null  float64
 1   X                    357949 non-null  float64
 2   Y                    357949 non-null  float64
 3   generico_denuncia    267287 non-null  object 
 4   especifico_denuncia  267287 non-null  object 
 5   modalidad_denuncia   267287 non-null  object 
 6   geometry             357949 non-null  object 
 7   distrito             357949 non-null  object 
dtypes: float64(3), object(5)
memory usage: 21.8+ MB
None

First few rows:


anio          X          Y             generico_denuncia  \
0  2016.0 -76.981288 -11.962999  DELITOS CONTRA EL PATRIMONIO   
1  2016.0 -76.996587 -12.081735  DELITOS CONTRA EL PATRIMONIO   
2  2016.0 -77.060582 -12.062533  DELITOS CONTRA EL PATRIMONIO   
3  2016.0 -77.061853 -12.052915  DELITOS CONTRA EL PATRIMONIO   
4  2016.0 -77.087286 -12.028719  DELITOS CONTRA EL PATRIMONIO   

  especifico_denuncia modalidad_denuncia                           geometry  \
0                ROBO               ROBO      POINT (-76.981288 -11.962999)   
1               HURTO  HURTO DE VEHICULO  POINT (-76.99658708 -12.08173502)   
2                ROBO      ROBO AGRAVADO  POINT (-77.06058167 -12.06253264)   
3               HURTO  HURTO DE VEHICULO  POINT (-77.06185304 -12.05291537)   
4               HURTO              HURTO  POINT (-77.08728638 -12.02871934)   

                 distrito  
0  SAN JUAN DE LURIGANCHO  
1                SAN LUIS  
2                    LIMA  
3                    LIMA  
4    SAN MARTIN DE PORRES

In [47]:
import h3

all_data['hex_id'] = all_data.apply(
    lambda r: h3.latlng_to_cell(r['Y'], r['X'], 7), axis=1
)


In [48]:

# 1) Conteo por (hex, distrito)
hex_dist_counts = (
    all_data
    .dropna(subset=['hex_id','distrito'])
    .groupby(['hex_id','distrito'])
    .size()
    .reset_index(name='n')
)

# 2) Totales por hex
totals = hex_dist_counts.groupby('hex_id')['n'].sum().rename('n_total').reset_index()

# 3) Une totales y calcula % por distrito en ese hex
hex_dist_all = hex_dist_counts.merge(totals, on='hex_id', how='left')
hex_dist_all['pct'] = hex_dist_all['n'] / hex_dist_all['n_total']

# 4) (opcional) una fila por hex con la lista de distritos y sus % (para reportes)
hex_to_distritos_lista = (
    hex_dist_all
    .sort_values(['hex_id','n'], ascending=[True, False])
    .groupby('hex_id')
    .agg(
        distritos=('distrito', lambda x: list(x)),
        n_por_distrito=('n', lambda x: list(x)),
        pct_por_distrito=('pct', lambda x: [float(round(v,4)) for v in x]),
        n_total=('n_total','first')
    )
    .reset_index()
)

# 5) (opcional) versión en string “amistosa” para CSV/tabla
hex_to_distritos_lista['distritos_str'] = hex_to_distritos_lista.apply(
    lambda r: '; '.join([f"{d} ({p*100:.1f}%)" for d,p in zip(r['distritos'], r['pct_por_distrito'])]),
    axis=1
)

# >> hex_dist_all: 1 fila por (hex, distrito) con n y pct
# >> hex_to_distritos_lista: 1 fila por hex con listas/resumen


In [50]:
hex_to_distritos_lista[hex_to_distritos_lista["hex_id"] == "878e62c0cffffff"]

hex_id                                distritos  \
89  878e62c0cffffff  [LIMA, LA VICTORIA, BREÑA, JESUS MARIA]   

              n_por_distrito                  pct_por_distrito  n_total  \
89  [10245, 2203, 1488, 318]  [0.7187, 0.1546, 0.1044, 0.0223]    14254   

                                        distritos_str  
89  LIMA (71.9%); LA VICTORIA (15.5%); BREÑA (10.4...

In [52]:
hex_to_distritos_lista.to_csv("hex_pordistrito.csv",index=False)

In [19]:
all_data["hex_id"].value_counts()

hex_id
878e62c0cffffff    14254
878e62c0dffffff    13644
878e62c2bffffff    10528
878e62c01ffffff     9545
878e62c0effffff     8868
                   ...  
878e62886ffffff        1
878e62d11ffffff        1
878e62830ffffff        1
878e75a63ffffff        1
878e75a4affffff        1
Name: count, Length: 260, dtype: int64

In [ ]:

df = all_data.copy()
df["anio"] = pd.to_numeric(df["anio"], errors="coerce").astype("Int64")

if "hex_id" not in df.columns or df["hex_id"].isna().any():
    df["hex_id"] = df.apply(lambda r: h3.latlng_to_cell(float(r["Y"]), float(r["X"]), 7), axis=1)

years = sorted([int(y) for y in df["anio"].dropna().unique()])
center_lima = [-12.05, -77.05]

per_year = (
    df.dropna(subset=["anio", "hex_id"])
      .groupby(["anio", "hex_id"])
      .size()
      .reset_index(name="n_delitos")
)
global_counts = (
    df.dropna(subset=["hex_id"])
      .groupby("hex_id")
      .size()
      .reset_index(name="n_delitos")
)

vmin = 0
vmax = max(global_counts["n_delitos"].max(),
           per_year["n_delitos"].max() if not per_year.empty else 1)

cmap = cm.LinearColormap(
    colors=["#ffffb2", "#fecc5c", "#fd8d3c", "#f03b20", "#bd0026"],
    vmin=vmin, vmax=vmax
).to_step(6)
cmap.caption = "Número de delitos (intensidad)"

def add_hex_layer(map_obj, counts_df, layer_name, show=True, opacity=0.65, max_hex=None):
    """
    counts_df: DataFrame con columnas ['hex_id','n_delitos']
    """
    fg = folium.FeatureGroup(name=layer_name, show=show)
    data = counts_df.copy()
    if max_hex:
        data = data.sort_values("n_delitos", ascending=False).head(max_hex)

    for _, row in data.iterrows():
        hex_id = row["hex_id"]
        n = int(row["n_delitos"])
        boundary = h3.cell_to_boundary(hex_id)   
        color = cmap(n)
        folium.Polygon(
            locations=boundary,
            weight=0.5,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=opacity,
            tooltip=f"{layer_name}<br>delitos: {n}<br>hex: {hex_id}",
        ).add_to(fg)

    fg.add_to(map_obj)

m = folium.Map(location=center_lima, zoom_start=11, tiles="CartoDB positron")


add_hex_layer(m, global_counts, layer_name="Global (2016–2023)", show=True)


for y in years:
    ycounts = per_year.loc[per_year["anio"] == y, ["hex_id", "n_delitos"]]

    add_hex_layer(m, ycounts, layer_name=f"Año {y}", show=(y == max(years)), max_hex=None)

cmap.add_to(m)

folium.LayerControl(collapsed=False).add_to(m)

m 

In [ ]:

from __future__ import annotations

import argparse
import json
import os
from dataclasses import dataclass
from typing import Dict, Optional, Tuple, List

import numpy as np
import pandas as pd

# Optional deps
try:
    import h3
    _HAS_H3 = True
except Exception:
    _HAS_H3 = False

from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.ensemble import RandomForestRegressor
from scipy.stats import spearmanr, pearsonr
from joblib import dump

# Try XGBoost if installed
_HAS_XGB = False
try:
    from xgboost import XGBRegressor
    _HAS_XGB = True
except Exception:
    pass


@dataclass
class Config:
    h3_res: int = 7
    min_year: int = 2016
    max_year: int = 2023
    train_end: int = 2021
    val_year: int = 2022
    test_year: int = 2023
    history_lags: Tuple[int, ...] = (1, 2, 3)  # create lag1..lag3
    rolling_windows: Tuple[int, ...] = (2, 3)  # rolling means over years
    random_state: int = 42
    top_categories: int = 8  # one-hot top N categories of generico_denuncia per hex-year
    outdir: str = "outputs"
    modeldir: str = "models"


def ensure_dirs(cfg: Config):
    os.makedirs(cfg.outdir, exist_ok=True)
    os.makedirs(cfg.modeldir, exist_ok=True)


def add_year_exposure(counts: pd.DataFrame) -> pd.DataFrame:
    year_totals = counts.groupby("anio")["n_delitos"].sum().rename("year_total").reset_index()
    out = counts.merge(year_totals, on="anio", how="left")
    out["rate"] = np.where(out["year_total"] > 0, out["n_delitos"] / out["year_total"], 0.0)
    return out


def normalize_schema(df: pd.DataFrame) -> pd.DataFrame:
    expected = ["anio", "X", "Y", "generico_denuncia", "especifico_denuncia",
                "modalidad_denuncia", "geometry", "distrito"]
    missing = [c for c in expected if c not in df.columns]
    if missing:
        raise ValueError(f"Faltan columnas requeridas: {missing}")
    out = df.copy()
    out["anio"] = pd.to_numeric(out["anio"], errors="coerce").astype("Int64")
    out["X"] = pd.to_numeric(out["X"], errors="coerce")
    out["Y"] = pd.to_numeric(out["Y"], errors="coerce")
    # Limpieza básica de strings
    for c in ["generico_denuncia", "especifico_denuncia", "modalidad_denuncia", "distrito"]:
        if c in out.columns:
            out[c] = out[c].astype("string").fillna(pd.NA).str.strip()
    return out


def add_h3(df: pd.DataFrame, cfg: Config) -> pd.DataFrame:
    if not _HAS_H3:
        raise RuntimeError("El paquete 'h3' no está instalado. pip install h3")
    out = df.copy()
    if "hex_id" not in out.columns or out["hex_id"].isna().any():
        # h3.latlng_to_cell(lat, lon, res) => (Y, X) = (lat, lon)
        out["hex_id"] = out.apply(lambda r: h3.latlng_to_cell(float(r["Y"]), float(r["X"]), cfg.h3_res), axis=1)
    return out


def compute_counts(df: pd.DataFrame, cfg: Config) -> pd.DataFrame:
    # counts per (anio, hex)
    base = (
        df.dropna(subset=["anio", "hex_id"])
          .groupby(["anio", "hex_id"])
          .size()
          .reset_index(name="n_delitos")
    )
    # ensure complete year-hex panel by forward/back fill zeros
    # First, pivot to wide to fill missing with 0, then back to long
    years = list(range(cfg.min_year, cfg.max_year + 1))
    wide = base.pivot_table(index="hex_id", columns="anio", values="n_delitos", fill_value=0)
    for y in years:
        if y not in wide.columns:
            wide[y] = 0
    wide = wide[years]
    long = wide.stack().reset_index()
    long.columns = ["hex_id", "anio", "n_delitos"]
    long["anio"] = long["anio"].astype(int)
    return long


def compute_category_shares(df: pd.DataFrame, cfg: Config) -> pd.DataFrame:
    # shares of generico_denuncia per (anio, hex)
    cats = (
        df.dropna(subset=["anio", "hex_id"])
          .groupby(["anio", "hex_id", "generico_denuncia"])
          .size()
          .reset_index(name="n")
    )
    # pick top-N categories overall to one-hot
    topN = (
        cats.groupby("generico_denuncia")["n"]
            .sum()
            .sort_values(ascending=False)
            .head(cfg.top_categories)
            .index.tolist()
    )
    cats["generico_top"] = cats["generico_denuncia"].where(cats["generico_denuncia"].isin(topN), "_OTROS_")
    total = cats.groupby(["anio", "hex_id"])["n"].sum().rename("tot").reset_index()
    cats = cats.merge(total, on=["anio", "hex_id"], how="left")
    cats["share"] = cats["n"] / cats["tot"].replace(0, np.nan)
    # keep only top categories (others can be merged into a single share)
    top_shares = (
        cats.assign(cat=cats["generico_top"])
            .groupby(["anio", "hex_id", "cat"])["share"]
            .sum()
            .reset_index()
    )
    # pivot: columns cat_share_*
    pivot = top_shares.pivot_table(index=["anio", "hex_id"], columns="cat", values="share", fill_value=0.0)
    pivot.columns = [f"share_cat_{c}" for c in pivot.columns]
    pivot = pivot.reset_index()
    return pivot


def build_features(counts: pd.DataFrame, shares: pd.DataFrame, cfg: Config) -> pd.DataFrame:
    df = counts.merge(shares, on=["anio", "hex_id"], how="left").fillna(0.0)
    df = df.sort_values(["hex_id", "anio"])
    for L in cfg.history_lags:
        df[f"lag_{L}"] = df.groupby("hex_id")["rate"].shift(L).fillna(0.0)

    for W in cfg.rolling_windows:
        df[f"roll_mean_{W}"] = df.groupby("hex_id")["rate"].apply(
            lambda s: s.shift(1).rolling(window=W, min_periods=1).mean()
        ).values
        df[f"roll_std_{W}"] = df.groupby("hex_id")["rate"].apply(
            lambda s: s.shift(1).rolling(window=W, min_periods=1).std()
        ).fillna(0.0).values

    if 1 in cfg.history_lags and 3 in cfg.history_lags:
        df["trend_3"] = df["lag_1"] - df["lag_3"]
    else:
        df["trend_3"] = 0.0

    df["anio"] = df["anio"].astype(int)
    return df



def split_time_aware(df_feat: pd.DataFrame, cfg: Config):
    train = df_feat[df_feat["anio"] <= cfg.train_end].copy()
    val   = df_feat[df_feat["anio"] == cfg.val_year].copy()
    test  = df_feat[df_feat["anio"] == cfg.test_year].copy()

    base_cols = ["lag_1","lag_2","lag_3","roll_mean_2","roll_mean_3","roll_std_2","roll_std_3","trend_3"]
    share_cols = [c for c in df_feat.columns if c.startswith("share_cat_")]
    feature_cols = base_cols + share_cols


    def filt(d):
        if not set(["lag_1","lag_2","lag_3"]).issubset(d.columns):
            return d
        return d.loc[(d[["lag_1","lag_2","lag_3"]].sum(axis=1) > 0) | (d["anio"] > d["anio"].min())].copy()

    train, val, test = filt(train), filt(val), filt(test)

    X_train, y_train = train[feature_cols].values, train["rate"].values
    X_val,   y_val   = val[feature_cols].values,   val["rate"].values
    X_test,  y_test  = test[feature_cols].values,  test["rate"].values

    meta = {
        "feature_cols": feature_cols,
        "n_train": len(train), "n_val": len(val), "n_test": len(test)
    }
    # adjuntar year_total para re-escala al evaluar
    train["_year_total"], val["_year_total"], test["_year_total"] = train["year_total"], val["year_total"], test["year_total"]
    return (X_train, y_train, train), (X_val, y_val, val), (X_test, y_test, test), meta



def train_model(X_train, y_train, X_val, y_val, cfg: Config):
    # Prefer XGBoost if available; otherwise RandomForest
    if _HAS_XGB:
        model = XGBRegressor(
            n_estimators=600,
            max_depth=6,
            subsample=0.9,
            colsample_bytree=0.9,
            learning_rate=0.05,
            reg_lambda=1.0,
            random_state=cfg.random_state,
            n_jobs=-1,
            tree_method="hist",
        )
        model.fit(X_train, y_train, eval_set=[(X_val, y_val)], verbose=False)
        algo = "xgboost"
    else:
        model = RandomForestRegressor(
            n_estimators=700,
            max_depth=None,
            min_samples_split=2,
            min_samples_leaf=1,
            max_features="sqrt",
            n_jobs=-1,
            random_state=cfg.random_state,
            oob_score=False,
        )
        model.fit(X_train, y_train)
        algo = "random_forest"
    return model, algo


def safe_mape(y_true, y_pred):
    y_true = np.array(y_true, dtype=float)
    y_pred = np.array(y_pred, dtype=float)
    denom = np.where(y_true == 0, 1.0, y_true)
    return float(np.mean(np.abs((y_true - y_pred) / denom)) * 100.0)


def eval_model(model, X, y, label: str):
    yhat = model.predict(X)
    mae = mean_absolute_error(y, yhat)
    # Compatibilidad con sklearn antiguo: RMSE = sqrt(MSE)
    mse = mean_squared_error(y, yhat)  # sin 'squared='
    rmse = float(np.sqrt(mse))
    r2 = r2_score(y, yhat)
    mape = safe_mape(y, yhat)
    # correlations
    try:
        sp = spearmanr(y, yhat).correlation
    except Exception:
        sp = np.nan
    try:
        pr = pearsonr(y, yhat)[0]
    except Exception:
        pr = np.nan
    return {
        "label": label,
        "MAE": mae,
        "RMSE": rmse,
        "R2": r2,
        "MAPE%": mape,
        "Spearman": float(sp) if sp is not None else np.nan,
        "Pearson": float(pr) if pr is not None else np.nan,
    }, yhat


def eval_model_counts(model, X, frame_with_year_total, y_true_counts, label: str):
    yhat_rate = model.predict(X)
    yhat_counts = yhat_rate * frame_with_year_total["_year_total"].values
    mae = mean_absolute_error(y_true_counts, yhat_counts)
    mse = mean_squared_error(y_true_counts, yhat_counts)
    rmse = float(np.sqrt(mse))
    r2 = r2_score(y_true_counts, yhat_counts)
    mape = safe_mape(y_true_counts, yhat_counts)
    # correlaciones
    try: sp = spearmanr(y_true_counts, yhat_counts).correlation
    except: sp = np.nan
    try: pr = pearsonr(y_true_counts, yhat_counts)[0]
    except: pr = np.nan
    return {
        "label": label, "MAE": mae, "RMSE": rmse, "R2": r2, "MAPE%": mape,
        "Spearman": float(sp) if sp is not None else np.nan,
        "Pearson": float(pr) if pr is not None else np.nan,
    }, yhat_counts


def feature_importance_df(model, feature_names: List[str]) -> pd.DataFrame:
    if hasattr(model, "feature_importances_"):
        imp = model.feature_importances_
    elif hasattr(model, "get_booster"):
        try:
            booster = model.get_booster()
            raw = booster.get_score(importance_type="gain")
            keys = list(raw.keys())
            vals = list(raw.values())
            return pd.DataFrame({"feature": keys, "importance": vals}).sort_values("importance", ascending=False)
        except Exception:
            imp = None
    else:
        imp = None

    if imp is None:
        return pd.DataFrame({"feature": feature_names, "importance": np.nan})
    return pd.DataFrame({"feature": feature_names, "importance": imp}).sort_values("importance", ascending=False)


def prepare_prediction_outputs(model, df_feat: pd.DataFrame, meta: Dict, cfg: Config):
    feature_cols = meta["feature_cols"]
    val  = df_feat[df_feat["anio"] == cfg.val_year].copy()
    test = df_feat[df_feat["anio"] == cfg.test_year].copy()

    def predict_counts(d):
        X = d[feature_cols].values
        yhat_rate = model.predict(X)
        yhat_cnt  = yhat_rate * d["year_total"].values
        out = d[["anio","hex_id","n_delitos","year_total"] + feature_cols].copy()
        out["y_pred"] = yhat_cnt
        out["y_pred_rate"] = yhat_rate
        return out

    val_pred  = predict_counts(val)
    test_pred = predict_counts(test)

    # 2024: usa 2023 como base de features; si no conoces year_total_2024,
    # puedes usar el mismo total de 2023 o un escenario (ej: promedio últimos 3 años)
    future_base = df_feat[df_feat["anio"] == cfg.test_year].copy()
    if not future_base.empty:
        Xf = future_base[feature_cols].values
        yhat_rate = model.predict(Xf)
        # Escenario de total anual (elige 1):
        # a) mismo total que 2023:
        year_total_2024 = future_base["year_total"].values
        # b) promedio 3 años:
        # year_total_2024 = future_base.groupby("anio")["year_total"].transform(lambda x: x.tail(3).mean()).values
        yhat_cnt = yhat_rate * year_total_2024
        future_base = future_base.copy()
        future_base["anio"] = cfg.test_year + 1
        future_base["n_delitos"] = np.nan
        future_base["year_total"] = year_total_2024
        future_base["y_pred"] = yhat_cnt
        future_base["y_pred_rate"] = yhat_rate
        future_2024 = future_base[["anio","hex_id","n_delitos","year_total","y_pred","y_pred_rate"] + feature_cols].copy()
    else:
        future_2024 = pd.DataFrame(columns=["anio","hex_id","n_delitos","year_total","y_pred","y_pred_rate"] + feature_cols)

    return val_pred, test_pred, future_2024



def run_pipeline(csv_path: Optional[str] = None, df: Optional[pd.DataFrame] = None, cfg: Optional[Config] = None):
    """
    Pipeline completo:
    - Normaliza y crea H3
    - Agrega conteos (anio, hex) y exposición anual (year_total), calcula 'rate'
    - Features (lags/rolling/trend sobre rate + shares de categorías)
    - Split temporal (train<=2021, val=2022, test=2023)
    - Entrena (XGB si disponible; si no RF)
    - Evalúa en CONTEOS re-escalando por exposición
    - Exporta métricas, importancias y predicciones (2023, escenario 2024)
    """
    cfg = cfg or Config()
    ensure_dirs(cfg)

    # 1) Cargar datos
    if df is None and csv_path is None:
        raise ValueError("Proporciona csv_path o df.")
    if df is None:
        df = pd.read_csv(csv_path)

    # 2) Normalizar y H3
    df = normalize_schema(df)
    df = add_h3(df, cfg)

    # 3) Agregaciones + exposición anual
    counts = compute_counts(df, cfg)          # ['hex_id','anio','n_delitos']
    counts = add_year_exposure(counts)        # + ['year_total','rate']

    # 4) Shares por tipo
    shares = compute_category_shares(df, cfg)

    # 5) Features (lags/rolling/trend sobre rate)
    feats = build_features(counts, shares, cfg)

    # 6) Split temporal
    (X_train, y_train, train_df), (X_val, y_val, val_df), (X_test, y_test, test_df), meta = split_time_aware(feats, cfg)

    # 7) Entrenamiento
    model, algo = train_model(X_train, y_train, X_val, y_val, cfg)

    # 8) Evaluación en CONTEOS (re-escalando por year_total)
    metrics = {}
    m_tr, _ = eval_model_counts(model, X_train, train_df, train_df["n_delitos"].values, label="train")
    m_va, _ = eval_model_counts(model, X_val,   val_df,   val_df["n_delitos"].values,   label="val")
    m_te, _ = eval_model_counts(model, X_test,  test_df,  test_df["n_delitos"].values,  label="test")

    for m in (m_tr, m_va, m_te):
        metrics[m["label"]] = {k: v for k, v in m.items() if k != "label"}

    # 9) Importancia de variables
    fi = feature_importance_df(model, meta["feature_cols"])

    # 10) Predicciones (val/test) y escenario 2024 re-escaladas
    val_pred, test_pred, future_2024 = prepare_prediction_outputs(model, feats, meta, cfg)

    # 11) Guardar artefactos
    with open(os.path.join(cfg.outdir, "metrics.json"), "w", encoding="utf-8") as f:
        json.dump({"algo": algo, "metrics": metrics, "n_rows": meta}, f, ensure_ascii=False, indent=2)

    fi_path = os.path.join(cfg.outdir, "feature_importance.csv")
    p23_path = os.path.join(cfg.outdir, "predictions_2023.csv")
    p24_path = os.path.join(cfg.outdir, "predictions_2024.csv")
    model_path = os.path.join(cfg.modeldir, "model.joblib")

    fi.to_csv(fi_path, index=False)
    test_pred.to_csv(p23_path, index=False)
    future_2024.to_csv(p24_path, index=False)
    dump(model, model_path)

    artifacts = {
        "algo": algo,
        "metrics": metrics,
        "feature_importance_path": fi_path,
        "predictions_2023_path": p23_path,
        "predictions_2024_path": p24_path,
        "model_path": model_path,
    }
    return artifacts, (feats, val_pred, test_pred, future_2024)



def main():
    parser = argparse.ArgumentParser(description="Spatial crime modeling pipeline (hex-based, time-aware).")
    parser.add_argument("--csv", type=str, default=None, help="Ruta a CSV con columnas requeridas.")
    args = parser.parse_args()

    cfg = Config()
    if args.csv is None:
        raise SystemExit("Proporciona --csv /ruta/datos.csv o usa run_pipeline(df=...) desde un notebook.")

    artifacts, _ = run_pipeline(csv_path=args.csv, cfg=cfg)
    print(json.dumps(artifacts, indent=2, ensure_ascii=False))


In [ ]:

cfg = Config(
    train_end=2022, 
    val_year=2022,  
    test_year=2023 
)

artifacts, (feats, val_pred, test_pred, future_2024) = run_pipeline(df=all_data, cfg=cfg)
print(artifacts)


{'algo': 'xgboost', 'metrics': {'train': {'MAE': 10.409015985876476, 'RMSE': 17.02510820539845, 'R2': 0.9940361419534535, 'MAPE%': 82.67218176867594, 'Spearman': 0.9632592459842776, 'Pearson': 0.9970766068799133}, 'val': {'MAE': 10.552423382880985, 'RMSE': 15.987294076659097, 'R2': 0.9941943446396897, 'MAPE%': 39.88203421415016, 'Spearman': 0.9847847201303057, 'Pearson': 0.9972052486919245}, 'test': {'MAE': 16.070894723624914, 'RMSE': 32.127870558577634, 'R2': 0.8985686743518254, 'MAPE%': 54.37834895962976, 'Spearman': 0.9709236953551073, 'Pearson': 0.9524240624002454}}, 'feature_importance_path': 'outputs\\feature_importance.csv', 'predictions_2023_path': 'outputs\\predictions_2023.csv', 'predictions_2024_path': 'outputs\\predictions_2024.csv', 'model_path': 'models\\model.joblib'}


In [31]:
artifacts, (feats, val_pred, test_pred, future_2024) = run_pipeline(df=all_data)

In [32]:
artifacts

{'algo': 'xgboost',
 'metrics': {'train': {'MAE': 10.159623302990834,
   'RMSE': 16.853420294357715,
   'R2': 0.9943217602061728,
   'MAPE%': 89.63407263202788,
   'Spearman': 0.9584872164968684,
   'Pearson': 0.9972229464122173},
  'val': {'MAE': 39.29225364498328,
   'RMSE': 77.38094019162806,
   'R2': 0.863990473572591,
   'MAPE%': 50.783342703647705,
   'Spearman': 0.9731173871860794,
   'Pearson': 0.9361985287763888},
  'test': {'MAE': 17.154884231313062,
   'RMSE': 34.31664140660389,
   'R2': 0.884277509452843,
   'MAPE%': 52.93816192480706,
   'Spearman': 0.9691927801758402,
   'Pearson': 0.9494691239536901}},
 'feature_importance_path': 'outputs\\feature_importance.csv',
 'predictions_2023_path': 'outputs\\predictions_2023.csv',
 'predictions_2024_path': 'outputs\\predictions_2024.csv',
 'model_path': 'models\\model.joblib'}

In [ ]:

import folium
import h3
import pandas as pd
import numpy as np
import branca.colormap as cm

def plot_predictions_map(csv_path: str, year_col: str = "anio",
                         value_col: str = "y_pred",  # usa 'n_delitos' para “real”
                         year: int | None = None,
                         vmax_percentile: float = 95,
                         top_n: int | None = None,
                         tiles: str = "CartoDB positron"):
    """
    Lee un CSV de predicciones (o reales) con columnas:
    ['anio','hex_id','y_pred', 'n_delitos', 'year_total', ...]
    y dibuja un choropleth H3.
    """
    dfp = pd.read_csv(csv_path)
    if year is not None:
        dfp = dfp[dfp[year_col] == year].copy()
    if dfp.empty:
        raise ValueError("No hay filas para ese año en el CSV.")

    # selecciona columnas necesarias
    dfp = dfp[["hex_id", value_col]].copy()
    dfp[value_col] = dfp[value_col].clip(lower=0)

    # opcional: limitar a top N hex para rendimiento
    if top_n is not None:
        dfp = dfp.sort_values(value_col, ascending=False).head(top_n).copy()

    vmax = float(np.percentile(dfp[value_col], vmax_percentile))
    vmin = 0.0
    cmap = cm.LinearColormap(
        ["#ffffb2", "#fecc5c", "#fd8d3c", "#f03b20", "#bd0026"],
        vmin=vmin, vmax=vmax
    ).to_step(6)
    cmap.caption = f"{value_col} (0–P{vmax_percentile})"

    # centro Lima
    m = folium.Map(location=[-12.05, -77.05], zoom_start=11, tiles=tiles)

    for _, row in dfp.iterrows():
        hex_id = row["hex_id"]
        val = float(row[value_col])
        color = cmap(min(val, vmax))
        boundary = h3.cell_to_boundary(hex_id)  # [(lat, lon), ...]

        folium.Polygon(
            locations=boundary,
            weight=0.6,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.75,
            tooltip=f"{value_col}: {val:.1f}<br>hex: {hex_id}",
        ).add_to(m)

    cmap.add_to(m)
    return m

# Ejemplos:
m_test = plot_predictions_map("outputs/predictions_2023.csv", value_col="y_pred", year=2023, vmax_percentile=95)
m_test  # o m_test.save("mapa_pred_2023.html")

m_2024 = plot_predictions_map("outputs/predictions_2024.csv", value_col="y_pred", year=2024, vmax_percentile=95)
m_2024  # o m_2024.save("mapa_pred_2024.html")


In [ ]:
import pandas as pd

pred23 = pd.read_csv("outputs/predictions_2023.csv")
top_hex_2023 = (pred23.sort_values("y_pred", ascending=False)
                        .head(15)[["hex_id", "y_pred"]])
print(top_hex_2023)



              hex_id      y_pred
89   878e62c0cffffff  484.516641
107  878e62c2bffffff  388.688345
85   878e62c08ffffff  375.224335
90   878e62c0dffffff  362.556918
79   878e62c01ffffff  343.304433
91   878e62c0effffff  308.537722
187  878e62d19ffffff  290.199762
134  878e62c56ffffff  288.098523
140  878e62c5dffffff  271.976459
108  878e62c2cffffff  260.823404
130  878e62c52ffffff  244.941408
106  878e62c2affffff  244.709544
189  878e62d1bffffff  238.601974
81   878e62c03ffffff  226.560224
103  878e62c26ffffff  226.367337


In [35]:
fi = pd.read_csv("outputs/feature_importance.csv")
fi.head(15)


feature  importance
0                                         roll_mean_3    0.435047
1                                         roll_mean_2    0.355665
2                                               lag_1    0.057561
3   share_cat_DELITOS CONTRA LA VIDA, EL CUERPO Y ...    0.023958
4                                          roll_std_3    0.021830
5              share_cat_DELITOS CONTRA EL PATRIMONIO    0.021512
6                                               lag_3    0.020308
7                                               lag_2    0.017085
8                                          roll_std_2    0.016770
9                                             trend_3    0.015530
10      share_cat_DELITOS CONTRA LA SEGURIDAD PÚBLICA    0.014732

In [53]:
import folium
import h3
import pandas as pd
import numpy as np
import branca.colormap as cm

def _hex_boundary(hex_id):
    # h3.cell_to_boundary devuelve [(lat, lon), ...] y Folium espera igual (lat, lon)
    return h3.cell_to_boundary(hex_id)

def _add_layer(m, df, value_col, layer_name, vmax_percentile=95, tooltip_cols=None):
    """Agrega una capa choropleth a un mapa Folium."""
    g = folium.FeatureGroup(name=layer_name, show=False)

    # Evita negativos y recorta colas para mejor contraste visual
    vals = df[value_col].clip(lower=0)
    vmax = float(np.percentile(vals, vmax_percentile)) if len(vals) else 1.0
    vmin = 0.0

    cmap = cm.LinearColormap(
        ["#ffffb2", "#fecc5c", "#fd8d3c", "#f03b20", "#bd0026"],
        vmin=vmin, vmax=vmax
    )
    cmap.caption = f"{layer_name} ({value_col})"

    for _, row in df.iterrows():
        hex_id = row["hex_id"]
        v = float(max(0, row[value_col]))
        color = cmap(min(v, vmax))
        boundary = _hex_boundary(hex_id)

        # Tooltip: valor + columnas adicionales si las hay
        tip_parts = [f"{value_col}: {v:.1f}", f"hex: {hex_id}"]
        if tooltip_cols:
            for c in tooltip_cols:
                if c in row and pd.notna(row[c]):
                    tip_parts.append(f"{c}: {row[c]}")
        tooltip_html = "<br>".join(tip_parts)

        folium.Polygon(
            locations=boundary,
            weight=0.6,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.75,
            tooltip=tooltip_html,
        ).add_to(g)

    g.add_to(m)
    cmap.add_to(m)

def map_resultados(csv_2023="outputs/predictions_2023.csv",
                   csv_2024="outputs/predictions_2024.csv",
                   top_n=None,
                   vmax_percentile=95,
                   tiles="CartoDB positron"):
    """
    Crea un mapa con 3 capas:
      - 2023 REAL (n_delitos)
      - 2023 PRED (y_pred)
      - 2024 PRED (y_pred)
    Si pasas 'top_n', limita a los top hex por valor para rendimiento.
    """
    # Carga
    df23 = pd.read_csv(csv_2023)
    df24 = pd.read_csv(csv_2024)

    # Asegura columnas mínimas
    needed = {"hex_id", "anio"}
    if not needed.issubset(df23.columns) or not needed.issubset(df24.columns):
        raise ValueError("Los CSV deben tener columnas al menos: hex_id, anio.")

    # Filtra año
    real23 = df23[["hex_id", "anio", "n_delitos"]].copy()
    pred23 = df23[["hex_id", "anio", "y_pred"]].copy()
    pred24 = df24[["hex_id", "anio", "y_pred"]].copy()

    real23 = real23[real23["anio"] == 2023].copy()
    pred23 = pred23[pred23["anio"] == 2023].copy()
    pred24 = pred24[pred24["anio"] == 2024].copy()

    # (Opcional) limitar a top_n por valor
    def _keep_top(d, col):
        if top_n is None:
            return d
        return d.sort_values(col, ascending=False).head(top_n).copy()

    real23 = _keep_top(real23, "n_delitos")
    pred23 = _keep_top(pred23, "y_pred")
    pred24 = _keep_top(pred24, "y_pred")

    # Mapa base centrado en Lima
    m = folium.Map(location=[-12.05, -77.05], zoom_start=11, tiles=tiles)

    # Capas
    _add_layer(m, real23, "n_delitos", "2023 REAL (n_delitos)", vmax_percentile=vmax_percentile)
    _add_layer(m, pred23, "y_pred", "2023 PRED (y_pred)", vmax_percentile=vmax_percentile)
    _add_layer(m, pred24, "y_pred", "2024 PRED (y_pred)", vmax_percentile=vmax_percentile)

    folium.LayerControl(collapsed=False).add_to(m)
    return m

# Uso:
m = map_resultados(
    csv_2023="outputs/predictions_2023.csv",
    csv_2024="outputs/predictions_2024.csv",
    top_n=None,           # o por ejemplo 300 para acelerar
    vmax_percentile=95,   # recorte de color para contraste
)
m  # en notebook
# m.save("mapa_predicciones_2023_2024.html")
